# Chapter 3: Data Collection and Pre-processing

Dear user, to help further analyse the design opportunities, \
you will now scrape data from several online sources for references.

In this notebook, you will scrape data from 4 different categories: \
**1. Social Media: Youtube**, \
**2. Social Media: Reddit**, \
**3. Websites**, \
**4. PDF File**

Each category will be using a different way to scrape data.

## TO DO SECTION

In [30]:
'''
Dear user, enter your Product here!
'''

product = "Scoot 787"

In [31]:
'''
Dear user, enter your online sources here (wherever required)!
'''

# In this notebook, we have pre-picked 5 online sources as follows:
### [1] Social Media: Youtube Comments
#       Please adjust the number of results to ensure a good sample size of 3000 - 5000 comments.
max_results = 15

### [2] Social Media: Reddit Comments
#       If you want a more focused dataset, do indicate a specific subreddit by editing the scrapping code below.
#       The link will be in such a format "https://oauth.reddit.com/your_subreddit_name/ ..." (for example, "https://oauth.reddit.com/r/aviation/ ...")
#       If not by default, the code will scrape from all subreddits.

### [3] Website: Article
#       Please indicate the url to your website:
url_3 = "https://www.planesportrait.com/post/scoot-468-flightreview"
###     Please inspect element on the website to find the most relevant container containing what you wish to scrape:
container_tag_3 = "div"
container_id_3 = None   # If the container has no id, please indicate None
container_class_3 = "MJXUU"

### [4] PDF File: Official Product Brochure (Online PDF)
#       Please indicate the url to your website: 
url_4 = "https://www.boeing.com/content/dam/boeing/boeingdotcom/commercial/airports/acaps/787.pdf"

### [5] PDF File: Textbook on Design of Aircrafts (Offline PDF)
#       Please indicate the url to your website:
url_5 = "others/Civil_Jet_Aircraft_Design.pdf"


## RUN AS INTENDED (DO NOT CHANGE ANYTHING.)

### Set Up

In [32]:
! pip install requests
! pip install python-dotenv
! pip install pdfminer.six
! pip install deep_translator

DEPRECATION: google-images-search 1.4.6 has a non-standard dependency specifier click>=7.0<=8.1.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of google-images-search or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


DEPRECATION: google-images-search 1.4.6 has a non-standard dependency specifier click>=7.0<=8.1.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of google-images-search or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


DEPRECATION: google-images-search 1.4.6 has a non-standard dependency specifier click>=7.0<=8.1.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of google-images-search or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


DEPRECATION: google-images-search 1.4.6 has a non-standard dependency specifier click>=7.0<=8.1.*. pip 24.1 will enforce this behaviour change. A possible replacement is to upgrade to a newer version of google-images-search or contact the author to suggest that they release a version with a conforming dependency specifiers. Discussion can be found at https://github.com/pypa/pip/issues/12063


In [33]:
search_terms = product

In [34]:
""" Create directory """
import os

try:                                              # Create directory named after search terms
    os.makedirs("support/%s" % search_terms)
    print("Directory", search_terms, "created")
except FileExistsError:
    print("Directory", search_terms, "exists")

Directory Scoot 787 exists


In [35]:
""" Save search terms """
import pickle

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))

### Data Collection

##### Category 1: Social Media Youtube

###### [1] Youtube Comments

In [36]:
""" Initialise and Set up Google API Key """
import os
from googleapiclient.discovery import build
from dotenv import load_dotenv

load_dotenv()

key = os.getenv("GOOGLE_API_KEY")

youtube = build('youtube', 'v3', developerKey=key)

file = "youtube"

In [37]:
""" Define containers to store info """
vid_id = []             	# video id
vid_page = []       		# video links (https...)
vid_title = []              # video title
num_comments = []           # official number of comments
load_error = 0              # error counter
can_load_title = []         # temp. list for storing title w/o loading error
can_load_page = []          # temp. list for storing links w/o loading error
num_page = []               # comment_response page number
page_title = []             # comment_response video title
comment_resp = []           # comment_response
comment_list = []           # temp. list for storing comments
comment_data = []           # comments & replies from comment_response
all_count = 0               # total number of comments

In [38]:
""" Search for Video IDs based on User Inputs """
print("Search for Videos IDs...")
request = youtube.search().list(
    q=search_terms,
    maxResults=max_results,
    part="id",
    type="video",
    order="relevance"         # Switch to "viewCount" if the number of comments are not sufficient
    )
search_response = request.execute()
print(search_response)

Search for Videos IDs...
{'kind': 'youtube#searchListResponse', 'etag': 'dF-wrnqBxCziaFsBWLCn7donnos', 'nextPageToken': 'CA8QAA', 'regionCode': 'SG', 'pageInfo': {'totalResults': 356063, 'resultsPerPage': 15}, 'items': [{'kind': 'youtube#searchResult', 'etag': '4yFR-rDAxbVJ4XYIgmPa3Zts9_Q', 'id': {'kind': 'youtube#video', 'videoId': 'Bx1uzMVPBtc'}}, {'kind': 'youtube#searchResult', 'etag': '3gZyv_5XgkvsPZkuNXYdjD0a0IE', 'id': {'kind': 'youtube#video', 'videoId': '6Iqx6P16ovY'}}, {'kind': 'youtube#searchResult', 'etag': 'knyhVdOvfQuUiJ2ycDTnhKNLsmQ', 'id': {'kind': 'youtube#video', 'videoId': 'R-wrdaaYBDk'}}, {'kind': 'youtube#searchResult', 'etag': 'MjERZs3FvcW6bTzYHA9Fyh-3cPU', 'id': {'kind': 'youtube#video', 'videoId': 'BCrqm7lTw_g'}}, {'kind': 'youtube#searchResult', 'etag': 'BTfhRfJwL6CwnIU-vrLAjYyqOVc', 'id': {'kind': 'youtube#video', 'videoId': 'OfL80kh430c'}}, {'kind': 'youtube#searchResult', 'etag': 'ADQn0os-Hhj0_G6mgoCkvCWH2T4', 'id': {'kind': 'youtube#video', 'videoId': 'yEHK

In [39]:
""" Create a list of Video IDs and a corresponding list of weblinks """
print("Videos found...")
for i in range(max_results):
    videoId = search_response['items'][i]['id']['videoId']
    print(videoId)
    vid_id.append(videoId)                          # a list of Video IDs
    page = "https://www.youtube.com/watch?v=" + videoId
    print(page)
    print()
    vid_page.append(page)                           # a list of Video links
print("\nThere are", len(vid_page), "videos.")

Videos found...
Bx1uzMVPBtc
https://www.youtube.com/watch?v=Bx1uzMVPBtc

6Iqx6P16ovY
https://www.youtube.com/watch?v=6Iqx6P16ovY

R-wrdaaYBDk
https://www.youtube.com/watch?v=R-wrdaaYBDk

BCrqm7lTw_g
https://www.youtube.com/watch?v=BCrqm7lTw_g

OfL80kh430c
https://www.youtube.com/watch?v=OfL80kh430c

yEHKbTkOHoU
https://www.youtube.com/watch?v=yEHKbTkOHoU

9REIyHF4xkk
https://www.youtube.com/watch?v=9REIyHF4xkk

wKtqcd33bg4
https://www.youtube.com/watch?v=wKtqcd33bg4

HxGs3uBGk8c
https://www.youtube.com/watch?v=HxGs3uBGk8c

NbtecD9hJXg
https://www.youtube.com/watch?v=NbtecD9hJXg

mHp41-PN1jo
https://www.youtube.com/watch?v=mHp41-PN1jo

-mb8oXY5psk
https://www.youtube.com/watch?v=-mb8oXY5psk

JFsZ9qNMEdU
https://www.youtube.com/watch?v=JFsZ9qNMEdU

WIe3Gj4hHks
https://www.youtube.com/watch?v=WIe3Gj4hHks

UqWKk8rlkVM
https://www.youtube.com/watch?v=UqWKk8rlkVM


There are 15 videos.


In [40]:
""" Use the list of Video IDs to get video data """
print("Get video data...")
for i in range(len(vid_id)):
    request = youtube.videos().list(
        part="snippet, statistics",
        id=vid_id[i]
        )
    video_response = request.execute()
    print(video_response)

    title = video_response['items'][0]['snippet']['title']
    vid_title.append(title)
    try:                        # use try/except as some videos might not load
        comment_count = video_response['items'][0]['statistics']['commentCount']
        print("Video", i + 1, "-", title, "-- Comment count: ", comment_count)
        print()
        num_comments.append(comment_count)
    except:
        print("Video", i + 1, "-", title, "-- Comments are turned off")
        print()
        num_comments.append(0)

Get video data...
{'kind': 'youtube#videoListResponse', 'etag': 'DtqPi-L2OJzIMApUDTHxPF1dl3g', 'items': [{'kind': 'youtube#video', 'etag': 'QsuiDSAPL5nFl1Io49X5OJ7KwPw', 'id': 'Bx1uzMVPBtc', 'snippet': {'publishedAt': '2023-02-26T11:30:02Z', 'channelId': 'UCEF-9XhkdyFY0hMRUkmxXfQ', 'title': "BRUTALLY HONEST | 13 Hours in Basic Economy Class on SCOOT's Boeing 787-8 from BERLIN to SINGAPORE!", 'description': 'Scoot is low cost airline owned by Singapore Airlines, but with a quality far away from their critically acclaimed parent, offering no meals, no headrests, no blankets and pillows. You get what you pay for.\n\nFOLLOW US ON INSTAGRAM FOR LIVE STORIES OF OUR FLIGHTS:\nhttps://www.instagram.com/Simply_Aviation\n\n*SOCIAL MEDIA*\nTWITTER: https://www.twitter.com/simply_aviation\nINSTAGRAM: https://www.instagram.com/Simply_Aviation\n\n*FLIGHT INFORMATION*\nAirline: Scoot\nAircraft: Boeing 787-8\nRegistration: 9V-OFI\nFlight Time: 12h 00min\nSeat: 33K\nFrom: Berlin Brandenburg\nTo: Singap

In [41]:
""" Use the list of Video IDs to get comments (by page) """
print("Get comment data...")
for i in range(len(vid_id)):
    try:                                        # use try/except as some "comments are turned off"
        request = youtube.commentThreads().list(
            part="snippet,replies",
            videoId=vid_id[i]
            )
        comment_response = request.execute()
        print(comment_response)

        comment_resp.append(comment_response)   # append 1 page of comment_response
        pages = 1
        num_page.append(pages)                  # append page number of comment_response
        page_title.append(vid_title[i])         # append video title along with the comment_response

        can_load_page.append(vid_page[i])       # drop link if it can't load (have at least 1 comment page)
        can_load_title.append(vid_title[i])     # drop title if it can't load (have at least 1 comment page)

        test = comment_response.get('nextPageToken', 'nil')         # check for nextPageToken
        while test != 'nil':                                        # keep running until last comment page
            next_page_ = comment_response.get('nextPageToken')
            request = youtube.commentThreads().list(
                part="snippet,replies",
                pageToken=next_page_,
                videoId=vid_id[i]
                )
            comment_response = request.execute()
            print(comment_response)

            comment_resp.append(comment_response)                   # append next page of comment_response
            pages += 1
            num_page.append(pages)                                  # append page number of comment_response
            page_title.append(vid_title[i])                         # append video title along with the comment_response

            test = comment_response.get('nextPageToken', 'nil')     # check for nextPageToken (while loop)
    except:
        load_error += 1

Get comment data...
{'kind': 'youtube#commentThreadListResponse', 'etag': '9aX-gjF54cytafD3ZCY_XB9pCAo', 'nextPageToken': 'Z2V0X25ld2VzdF9maXJzdC0tQ2dnSWdBUVZGN2ZST0JJRkNLZ2dHQUFTQlFpSklCZ0FFZ1VJaUNBWUFCSUZDSjBnR0FFU0JRaUhJQmdBR0FBaURnb01DTkNveWEwR0VPRGJ4S3dC', 'pageInfo': {'totalResults': 20, 'resultsPerPage': 20}, 'items': [{'kind': 'youtube#commentThread', 'etag': '5hJ6who4DfnEM3315XfGkuC_eD0', 'id': 'UgxaI_uwVHg6UgB9b9x4AaABAg', 'snippet': {'channelId': 'UCEF-9XhkdyFY0hMRUkmxXfQ', 'videoId': 'Bx1uzMVPBtc', 'topLevelComment': {'kind': 'youtube#comment', 'etag': '830GonIHFffV5XOWd4nWI0UGjXo', 'id': 'UgxaI_uwVHg6UgB9b9x4AaABAg', 'snippet': {'channelId': 'UCEF-9XhkdyFY0hMRUkmxXfQ', 'videoId': 'Bx1uzMVPBtc', 'textDisplay': 'I went in this airline the service wasn’t good I almost slept the whole flight without eating and entertainment but I guess every airline doesn’t have tv’s so I just decided airlines with tv’s is not always the best I learned my lesson the non-tv’s are the same as tv

In [42]:
""" Show videos without loading errors """
print("Videos that can load...")
vid_page = can_load_page                    # update vid_page with those with no load error
vid_title = can_load_title                  # update vid_title with those with no load error
for i in range(len(vid_title)):
    if vid_title[i] == 'YouTube':           # default error title is 'YouTube'
        vid_title[i] = 'Video_' + str(i+1)  # replace 'YouTube' with Video_1 format
    print(i + 1, vid_title[i])

Videos that can load...
1 BRUTALLY HONEST | 13 Hours in Basic Economy Class on SCOOT's Boeing 787-8 from BERLIN to SINGAPORE!
2 The Making Of Our 1st Boeing 787 Dreamliner - Scoot
3 Review: FLY SCOOT 787 - THE WORLD's WORST DREAMLINER?
4 TRIP REPORT | Scoot 787-8 | Seoul (ICN) to Singapore (SIN) | Economy Class
5 SCOOT 787-9 & A321NEO Melbourne to Hong Kong via Singapore
6 360° view of our Boeing 787 Dreamliner - Scoot
7 Is SCOOT 787 BUSINESS CLASS worth the MONEY?
8 Watch this BEFORE flying with SCOOT! | Singapore - Manila onboard a 787-8
9 Flying with Scoot as “Air-pprentice” - What Passengers Don’t See!
10 Trip Report: ScootPlus Singapore to Sydney Pokemon 787 Scoot Airlines Business Class
11 TRIPREPORT | Scoot (BUSINESS) | Boeing 787-8 | Taipei Taoyuan - Singapore
12 [TRIP REPORT] Scoot Flight 16 - Boeing 787-9 Dreamliner - Singapore » Perth (ScootPlus)
13 SCOOT Economy Class (Boeing 787-9) (Seat 9A)
14 SCOOT BOEING 787-9 BALI KE SINGAPURA! INTERIORNYA WARNA-WARNI KAYAK BUS AKAP!
1

In [43]:
""" Sift through and store comments as a list """
print("Get individual comment...")
for k in range(len(comment_resp)):
    count = 0                                                     # comment counter
    comments_found = comment_resp[k]['pageInfo']['totalResults']  # comments on 1 comment_response page
    count = count + comments_found
    for i in range(comments_found):
        try:
            comment_list.append(comment_resp[k]['items'][i]['snippet']['topLevelComment']['snippet']['textDisplay'])
            print(comment_resp[k]['items'][i]['snippet']['topLevelComment']['snippet']['textDisplay'])
        except:
            print("missing comment")                              # or too many comments (e.g. 7.3K comments)

print(comment_list)
print()
print(len(comment_list), "comments in total.")

Get individual comment...
I went in this airline the service wasn’t good I almost slept the whole flight without eating and entertainment but I guess every airline doesn’t have tv’s so I just decided airlines with tv’s is not always the best I learned my lesson the non-tv’s are the same as tv’s for a good 787 is the first scoot flight I had I think they should have these planes to bring back: 747 757 A340 A380 717 727 737-232
I love the idea of silent economy which is just economy plus with no children screaming. 👍
Thanks for your video. One question. Which kind of plug your seat had? Was that compatible with a C type? thanks.
I’ll be your guide on how to survive scoot long haul flights<br> <br>1.bring a power bank fully charged<br><br>2.bring some snacks with you onboard<br><br>3.bring a gaming handheld to play some games to kill some time<br><br>4.bring your own amenities like eye masks,earplugs,toothbrushes and toothpaste
one hour in economy flight
For me, 4 hours it can be very unc

In [44]:
""" Saving files! """
import pickle
import os

try: 
    os.makedirs("support/%s/%s" % (search_terms, file))
    print("Directory", file, "created")
except FileExistsError:
    print("Directory", file, "exists")

f = open("support/%s/%s/comment_list.txt" % (search_terms, file), "w+", encoding="utf-8")
for i in range(len(comment_list)):
    f.write("<<<" + comment_list[i] + ">>>")
f.close()

pickle.dump(comment_list, open("support/%s/%s/comment_list.pkl" % (search_terms, file), "wb"))
pickle.dump(vid_title, open("support/%s/%s/vid_title.pkl" % (search_terms, file), "wb"))
pickle.dump(vid_page, open("support/%s/%s/vid_page.pkl" % (search_terms, file), "wb"))
pickle.dump(vid_id, open("support/%s/%s/vid_id.pkl" % (search_terms, file), "wb"))

Directory youtube exists


##### Category 2: Social Media Reddit

###### [2] Reddit Comments

In [45]:
""" Initialise and Set up Reddit API """
import requests
import os
from dotenv import load_dotenv

load_dotenv()

id = os.getenv("REDDIT_API_ID")
key = os.getenv("REDDIT_API_KEY")
user = os.getenv("REDDIT_API_USER")
pw = os.getenv("REDDIT_API_PW")

auth = requests.auth.HTTPBasicAuth(id, key)

data = {'grant_type': 'password',                                       # Initalize using login method (password), username, and password
        'username': user,
        'password': pw}

headers = {'User-Agent': 'DAI/AID'}                                     # Setup our header info, which gives reddit a brief description of our app

res = requests.post('https://www.reddit.com/api/v1/access_token',       # Send request for an OAuth token
                    auth=auth, data=data, headers=headers)

TOKEN = res.json()['access_token']                                      # Convert response to JSON and pull access_token value

headers = {**headers, **{'Authorization': f"bearer {TOKEN}"}}

requests.get('https://oauth.reddit.com/api/v1/me', headers=headers)     # Token is valid for ~2 hours. If get Response [200], you are good to go!

file = "reddit"

In [46]:
""" Define containers to store info """
post_id = []             	     # post id
post_page = []       		     # post links (https...)
post_title = []                  # post title
post_num_comments = []           # official number of comments
comment_list = []           # temp. list for storing comments

In [47]:
""" Search for Post IDs based on User Inputs """
print("Search for Post IDs...")
res = requests.get(f"https://oauth.reddit.com/search/?q={search_terms}&restrict_sr=on&sort=relevance&t=all",
                   headers=headers)

if res.status_code == 200:                  # Check if the request was successful
    search_response = res.json()            # Parse the response as JSON
    print(search_response)
else:
    print(f"Error: {res.status_code} - {res.reason}")

Search for Post IDs...
{'kind': 'Listing', 'data': {'modhash': None, 'dist': 25, 'facets': {}, 'after': 't3_8841i3', 'geo_filter': '', 'children': [{'kind': 't3', 'data': {'approved_at_utc': None, 'subreddit': 'aviation', 'selftext': '', 'author_fullname': 't2_uqnzx562', 'saved': False, 'mod_reason_title': None, 'gilded': 0, 'clicked': False, 'title': 'Scoot 787 loses nose wheel on approach to Taipei', 'link_flair_richtext': [], 'subreddit_name_prefixed': 'r/aviation', 'hidden': False, 'pwls': 6, 'link_flair_css_class': '', 'downs': 0, 'thumbnail_height': 78, 'top_awarded_type': None, 'hide_score': False, 'name': 't3_14ddn9v', 'quarantine': False, 'link_flair_text_color': 'dark', 'upvote_ratio': 0.99, 'author_flair_background_color': None, 'ups': 534, 'total_awards_received': 0, 'media_embed': {}, 'thumbnail_width': 140, 'author_flair_template_id': None, 'is_original_content': False, 'user_reports': [], 'secure_media': None, 'is_reddit_media_domain': True, 'is_meta': False, 'category':

In [48]:
""" Create a list of Post IDs and a corresponding list of weblinks """
print("Posts found...")

for post in search_response['data']['children']:
    postId = post['data']['id']
    print(postId)
    post_id.append(postId)                           # a list of Post IDs
    page = f"https://oauth.reddit.com/comments/{postId}"
    print(page)
    print()
    post_page.append(page)                           # a list of Post links

print(f"\nThere are {len(post_page)} posts.")

Posts found...
14ddn9v
https://oauth.reddit.com/comments/14ddn9v

14j4d5q
https://oauth.reddit.com/comments/14j4d5q

15gcc5u
https://oauth.reddit.com/comments/15gcc5u

wnco66
https://oauth.reddit.com/comments/wnco66

10ox4yb
https://oauth.reddit.com/comments/10ox4yb

11ca06x
https://oauth.reddit.com/comments/11ca06x

wodfah
https://oauth.reddit.com/comments/wodfah

r4s64g
https://oauth.reddit.com/comments/r4s64g

pe66v2
https://oauth.reddit.com/comments/pe66v2

scjt7x
https://oauth.reddit.com/comments/scjt7x

qs7w2k
https://oauth.reddit.com/comments/qs7w2k

6i4hqx
https://oauth.reddit.com/comments/6i4hqx

oq4y50
https://oauth.reddit.com/comments/oq4y50

3yb89o
https://oauth.reddit.com/comments/3yb89o

qflq1r
https://oauth.reddit.com/comments/qflq1r

83gzl8
https://oauth.reddit.com/comments/83gzl8

80lk4h
https://oauth.reddit.com/comments/80lk4h

qsex07
https://oauth.reddit.com/comments/qsex07

qs727k
https://oauth.reddit.com/comments/qs727k

2oplry
https://oauth.reddit.com/comments/2op

In [49]:
""" Use the list of Post IDs to get post data """
print("Get post data...")
for i, post_response in enumerate(search_response['data']['children']):
    try:
        print(post_response)
        title = post_response['data']['title']                                  # Extract title and comment count from post response
        post_title.append(title)
        comment_count = post_response['data']['num_comments']
        print(f"Post {i + 1} - {title} -- Comment count: {comment_count}")
        post_num_comments.append(comment_count)
        print()
        
    except Exception as e:
        print(f"Error fetching post data: {e}")

print(sum(post_num_comments), "comments in total.")

Get post data...
{'kind': 't3', 'data': {'approved_at_utc': None, 'subreddit': 'aviation', 'selftext': '', 'author_fullname': 't2_uqnzx562', 'saved': False, 'mod_reason_title': None, 'gilded': 0, 'clicked': False, 'title': 'Scoot 787 loses nose wheel on approach to Taipei', 'link_flair_richtext': [], 'subreddit_name_prefixed': 'r/aviation', 'hidden': False, 'pwls': 6, 'link_flair_css_class': '', 'downs': 0, 'thumbnail_height': 78, 'top_awarded_type': None, 'hide_score': False, 'name': 't3_14ddn9v', 'quarantine': False, 'link_flair_text_color': 'dark', 'upvote_ratio': 0.99, 'author_flair_background_color': None, 'ups': 534, 'total_awards_received': 0, 'media_embed': {}, 'thumbnail_width': 140, 'author_flair_template_id': None, 'is_original_content': False, 'user_reports': [], 'secure_media': None, 'is_reddit_media_domain': True, 'is_meta': False, 'category': None, 'secure_media_embed': {}, 'link_flair_text': 'News', 'can_mod_post': False, 'score': 534, 'approved_by': None, 'is_created_f

In [50]:
""" Sift through and store comments as a list """
print("Get individual comment...")

def scrape_comments(url, comment_list):
    try:
        page_json = f"{url}.json"

        post_comments_response = requests.get(page_json, headers=headers) 
        if post_comments_response.status_code == 200:                                       # Check if request was successful
            post_comments_data = post_comments_response.json()
            if isinstance(post_comments_data, list) and len(post_comments_data) > 1:
                total_comments = post_comments_data[1]['data']['children'][0]['data']['total_awards_received']
                print(f"Total comments: {total_comments}")
                comments = post_comments_data[1]['data']['children']                        # Extract comments from the response
                for comment in comments:
                    try:
                        comment_body = comment['data']['body']
                        print(comment_body)
                        comment_list.append(comment_body)
                        if 'replies' in comment['data'] and comment['data']['replies']:     # Check for replies and recursively scrape them
                            scrape_replies(comment['data']['replies']['data']['children'], comment_list)
                    except KeyError:
                        print("Error: Missing 'body' attribute for a comment.")
        else:
            print(f"Error fetching comments for page {url}: {post_comments_response.status_code} - {post_comments_response.reason}")
    except Exception as e:
        print(f"Error fetching comments for page {url}:", e)

def scrape_replies(replies, comment_list):                                                  # Function to scrape replies recursively
    for reply in replies:
        try:
            reply_body = reply['data']['body']
            print(reply_body)
            comment_list.append(reply_body)
            # Recursively scrape replies of replies
            if 'replies' in reply['data'] and reply['data']['replies']:
                scrape_replies(reply['data']['replies']['data']['children'], comment_list)
        except KeyError:
            print("Error: Missing 'body' attribute for a reply.")

for page in post_page:
    scrape_comments(page, comment_list)

print(comment_list)
print()
print(len(comment_list), "valid comments in total.")

Get individual comment...
Total comments: 0
Shows how good the redundancy engineering is I guess, able to land safely on a single wheel!

Article didn't mention it, does anyone know if it was able to taxi by itself or did it stop on the runway and wait for a tow?
According to avherald it taxied in unaware of the missing wheel:

https://avherald.com/h?article=50aa80cb&amp;opt=0
Impressive! Thanks for the link.
Even more impressive that they didn't even notice it was missing.
Or that nobody on the ground saw it and reported it…
The departure airport apparently reported Tire fragments on the runway after takeoff. The arrival airport was notified to be on alert when it landed.
They did, you can clearly see them take cell phones pictures to post on Reddit for karma in that picture.  It’s kind of a Redditception Reddit post of a Reddit post.
thats why there is 2 of them
These nose wheels are getting out of hand.
Well, some sukhoi su27 only got one nosewheel
Right well one weighs 18 tons and 

In [51]:
""" Saving files! """
import pickle
import os

try: 
    os.makedirs("support/%s/%s" % (search_terms, file))
    print("Directory", file, "created")
except FileExistsError:
    print("Directory", file, "exists")

f = open("support/%s/%s/comment_list.txt" % (search_terms, file), "w+", encoding="utf-8")
for i in range(len(comment_list)):
    f.write("<<<" + comment_list[i] + ">>>")
f.close()

pickle.dump(comment_list, open("support/%s/%s/comment_list.pkl" % (search_terms, file), "wb"))
pickle.dump(post_title, open("support/%s/%s/post_title.pkl" % (search_terms, file), "wb"))
pickle.dump(post_page, open("support/%s/%s/post_page.pkl" % (search_terms, file), "wb"))
pickle.dump(post_id, open("support/%s/%s/post_id.pkl" % (search_terms, file), "wb"))

Directory reddit exists


##### Category 3: Websites

In [52]:
""" Scrape Data from Website Helper Function """
import requests
from bs4 import BeautifulSoup
import re

def extract_text_from_web(url, container_tag, container_id, container_class):
    response = requests.get(url)

    if response.status_code == 200:                                     # Check if the request was successful
        soup = BeautifulSoup(response.content, 'html.parser')           # Parse the HTML content

        title_tag = soup.find("title")                                  # Get the title of the webpage if it exists
        if title_tag:
            title = title_tag.get_text()
            print("Title:", title)
        else:
            print("No title found")

        extract = ""
        text = soup.find_all(container_tag, id=container_id, class_=container_class)     # Get text from the container containing the product description
        for i in range(len(text)):
            # Simple Cleaning of Text
            text[i] = re.sub(r'<script.*?</script>', '', str(text[i]), flags=re.DOTALL)     # Remove JavaScript stuff
            text[i] = re.sub(r'<style.*?</style>', '', text[i], flags=re.DOTALL)     # Remove CSS styles
            text[i] = re.sub(r'<.*?>', ' ', text[i])  # Remove HTML tags
            text[i] = text[i].replace('\n', ' ')           # Remove newline characters
            text[i] = re.sub(r'\s+', ' ', text[i].strip()) # Remove extra whitespace
            extract += text[i]

        return extract

    else:
        print("Failed to retrieve webpage. Status code:", response.status_code)

###### [3] Modern Airliners Article

In [53]:
""" Initalize """
file = "article"

url = url_3
container_tag = container_tag_3
container_id = container_id_3
container_class = container_class_3

In [54]:
""" Scrape Data from Website """
scrape_data = extract_text_from_web(url, container_tag, container_id, container_class)

print(scrape_data)

Title: Scoot 468 Flight Review &  A First-Timer's Boeing 787  Experience
Airline | Scoot Flight | TR468 Route | Singapore – Kuala Lumpur Gate | B9 Aircraft | Boeing 787-9 Registration | 9V-OJG Class of Travel | Economy Class Seat Number | 13K This is not only my first flight on Scoot, Singapore Airlines' low-cost subsidiary, but also my first flight on the Boeing 787 Dreamliner. When it came time to book my tickets, I had a plethora of options ranging from low-cost airlines like AirAsia to full-service carriers like Singapore Airlines, but I eventually settled on Scoot because it was one of the more affordable options. Flying with Scoot Checking in took an eternity. I was met with an uncomfortably long line. I'm not sure why, but I'm guessing the Scoot document checks take forever. However, when it was my turn, we were allowed in with a simple flip of our passports. If you check in at Terminal 1 and happen to pass by the Scoot check-in counter at a certain time, you will notice the end

In [55]:
""" Saving files! """
import pickle
import os
import nltk
nltk.download('punkt')

try: 
    os.makedirs("support/%s/%s" % (search_terms, file))
    print("Directory", search_terms, "created")
except FileExistsError:
    print("Directory", search_terms, "exists")

sentences = nltk.sent_tokenize(scrape_data)
f = open("support/%s/%s/%s.txt" % (search_terms, file, file), "w+", encoding="utf-8")
for sentence in sentences:
    f.write("<<<" + sentence.strip() + ">>>\n")
f.close()

pickle.dump(scrape_data, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))

Directory Scoot 787 exists


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\tanhu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


#### Category 4: PDF Files

In [56]:
""" Scrape Data from PDF """
import requests
import os
from pdfminer.high_level import extract_text

def extract_text_from_pdf(path_or_url):
    if path_or_url.startswith("http"):  # If it's a URL
        response = requests.get(path_or_url)
        with open('file.pdf', 'wb') as f:
            f.write(response.content)
        pdf_file_path = 'file.pdf'
    else:  # If it's a local file path
        pdf_file_path = path_or_url

    text = extract_text(pdf_file_path)

    text = text.replace('\n', ' ')
    text = text.replace("   ", ' ')                 
    text = text.replace("  ", ' ') 

    return text

###### [4] Official Boeing Airport Planning Paper (Online Brochure)

In [57]:
""" Initalize """
file = "brochure"
url = url_4

In [58]:
""" Scrape Data from PDF """
scrape_data = extract_text_from_pdf(url)
os.remove('file.pdf')

print(scrape_data)

CAGE Code 81205 787 Airplane Characteristics for Airport Planning DOCUMENT NUMBER: D6-58333 REVISION: REV O REVISION DATE: February 2023 CONTENT OWNER: Boeing Commercial Airplanes All revisions to this document must be approved by the content owner before release. Not Subject to US Export Administration Regulations (EAR), (15 C.F.R. Parts 730-774) or US International Traffic in Arms Regulations (ITAR), (22 C.F.R. Parts 120-130). Copyright © 2023 Boeing. All Rights Reserved.    Revision Record O December 2022 Section 6: Inlet Hazard Areas, all models Section 7: ACR Information, all models N October 2021 All sections: Standardize format, titles, notes. Section 2: Update ground clearances. Section 3: Update performance data. Section 4: Update turn radius data. Section 5: Update servicing arrangements and turntime analysis. Section 7: Update landing gear loading on pavement data. M March 2018 Update 787-10 data. All L December 2015 Initial release of 787-10 data. All K November 2014 All J

In [59]:
""" Saving files! """
import pickle
import os
import nltk
nltk.download('punkt')

try: 
    os.makedirs("support/%s/%s" % (search_terms, file))
    print("Directory", search_terms, "created")
except FileExistsError:
    print("Directory", search_terms, "exists")

sentences = nltk.sent_tokenize(scrape_data)
f = open("support/%s/%s/%s.txt" % (search_terms, file, file), "w+", encoding="utf-8")
for sentence in sentences:
    f.write("<<<" + sentence.strip() + ">>>\n")
f.close()

pickle.dump(scrape_data, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))

Directory Scoot 787 exists


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\tanhu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


###### [5] Textbook on Design of Aircrafts (Offline PDF)

In [60]:
""" Initalize """
file = "textbook"
url = url_5

In [61]:
""" Scrape Data from PDF """
scrape_data = extract_text_from_pdf(url)

print(scrape_data)

Civil Jet Aircraft Design Lloyd R. Jenkinson Senior Lecturer, Loughborough University, UK Paul Simpkin Formerly Head of Aircraft Performance, Rolls Royce, UK Darren Rhodes Civil Aviation Authority - NATS Department of Operational Research and Analysis (DORA), UK ARNOLD A member of the Hodder Headline Group LONDON • SYDNEY • AUCKLAND First published in Great Britain in 1999 by Arnold, a member of the Hodder Headline Group, 338 Euston Road, London NWl 3BH http://www.arnoldpublishers.com Co-published in North America by American Institute of Aeronautics and Astronautics, Inc., 1801 Alexander Bell Drive, Reston, VA 20191-4344 © 1999 Lloyd R. Jenkinson, Paul Simpkin and Darren Rhodes All rights reserved. No part of this publication may be reproduced or transmitted in any form or by any means, electronically or mechanically, including photocopying, recording or any information storage or retrieval system, without either prior permission in writing from the publisher or a licence permitting

In [62]:
""" Saving files! """
import pickle
import os
import nltk
nltk.download('punkt')

try: 
    os.makedirs("support/%s/%s" % (search_terms, file))
    print("Directory", search_terms, "created")
except FileExistsError:
    print("Directory", search_terms, "exists")

sentences = nltk.sent_tokenize(scrape_data)
f = open("support/%s/%s/%s.txt" % (search_terms, file, file), "w+", encoding="utf-8")
for sentence in sentences:
    f.write("<<<" + sentence.strip() + ">>>\n")
f.close()

pickle.dump(scrape_data, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))

Directory Scoot 787 exists


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\tanhu\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


### Further Preprocessing

In [63]:
""" Initialise and Establish Dataset """
import pandas as pd

youtube_comment_list = pd.read_pickle("support/%s/youtube/comment_list.pkl" % search_terms)
reddit_comment_list = pd.read_pickle("support/%s/reddit/comment_list.pkl" % search_terms)
article = pd.read_pickle("support/%s/article/article.pkl" % search_terms)
brochure = pd.read_pickle("support/%s/brochure/brochure.pkl" % search_terms)
textbook = pd.read_pickle("support/%s/textbook/textbook.pkl" % search_terms)

print("Search terms:", search_terms)
print("Number of Youtube comments:", len(youtube_comment_list))
print("Number of Reddit comments:", len(reddit_comment_list))
print("Length of Article:", len(article))
print("Length of Brochure:", len(brochure))
print("Length of Textbook:", len(textbook))

Search terms: Scoot 787
Number of Youtube comments: 2818
Number of Reddit comments: 125
Length of Article: 5517
Length of Brochure: 107410
Length of Textbook: 731054


In [64]:
""" Translate to English """
from deep_translator import GoogleTranslator

def translate_to_en(comment_list):
    for i in range(len(comment_list)):        # translate all
        try:
            comment_list[i] = GoogleTranslator(source='auto', target='en').translate(str(comment_list[i]))
        except:
            comment_list[i] = ''              # Omitted as exceeded 5000 characters.

print("Translating Youtube comments...")
translate_to_en(youtube_comment_list)
print(youtube_comment_list)
print()
print("Translating Reddit comments...")
translate_to_en(reddit_comment_list)
print(reddit_comment_list)

Translating Youtube comments...
['I went in this airline the service wasn’t good I almost slept the whole flight without eating and entertainment but I guess every airline doesn’t have tv’s so I just decided airlines with tv’s is not always the best I learned my lesson the non-tv’s are the same as tv’s for a good 787 is the first scoot flight I had I think they should have these planes to bring back: 747 757 A340 A380 717 727 737-232', 'I love the idea of silent economy which is just economy plus with no children screaming. 👍', 'Thanks for your video. One question. Which kind of plug your seat had? Was that compatible with a C type? thanks.', 'I’ll be your guide on how to survive scoot long haul flights<br> <br>1.bring a power bank fully charged<br><br>2.bring some snacks with you onboard<br><br>3.bring a gaming handheld to play some games to kill some time<br><br>4.bring your own amenities like eye masks,earplugs,toothbrushes and toothpaste', 'one hour in economy flight', 'For me, 4 h

In [65]:
""" Clean Text """
import re

def clean_text(text):                               # user defined function for cleaning text
    if text is None:
        return ("")
    else:
      text = text.lower()                             # all lower case
      text = re.sub(r'\[.*?\]', ' ', text)            # remove text within [ ] (' ' instead of '')
      text = re.sub(r'\<.*?\>', ' ', text)            # remove text within < > (' ' instead of '')
      text = re.sub(r'http\S+', ' ', text)            # remove website ref http
      text = re.sub(r'www\S+', ' ', text)             # remove website ref www

      text = text.replace('€', 'euros')               # replace special character with words
      text = text.replace('£', 'gbp')                 # replace special character with words
      text = text.replace('$', 'dollar')              # replace special character with words
      text = text.replace('%', 'percent')             # replace special character with words
      text = text.replace('\n', ' ')                  # remove \n in text that has it

      text = text.replace('\'', '’')                  # standardise apostrophe
      text = text.replace('&#39;', '’')               # standardise apostrophe

      text = text.replace('’d', ' would')             # remove ’ (for would, should? could? had + PP?)
      text = text.replace('’s', ' is')                # remove ’ (for is, John's + N?)
      text = text.replace('’re', ' are')              # remove ’ (for are)
      text = text.replace('’ll', ' will')             # remove ’ (for will)
      text = text.replace('’ve', ' have')             # remove ’ (for have)
      text = text.replace('’m', ' am')                # remove ’ (for am)
      text = text.replace('can’t', 'can not')         # remove ’ (for can't)
      text = text.replace('won’t', 'will not')        # remove ’ (for won't)
      text = text.replace('n’t', ' not')              # remove ’ (for don't, doesn't)

      text = text.replace('’', ' ')                   # remove apostrophe (in general)
      text = text.replace('&quot;', ' ')              # remove quotation sign (in general)

      text = text.replace('cant', 'can not')          # typo 'can't' (note that cant is a proper word)
      text = text.replace('dont', 'do not')           # typo 'don't'

      text = re.sub(r'[^a-zA-Z0-9]', r' ', text)      # only alphanumeric left
      text = text.replace("   ", ' ')                 # remove triple empty space
      text = text.replace("  ", ' ')                  # remove double empty space
      return text

def clean(text_list):
    cleaned_list = []
    for t in text_list:
        cleaned_list.append(clean_text(t))
    return cleaned_list

print("Cleaning Youtube comments...")
youtube_comment_list = clean(youtube_comment_list)
print(youtube_comment_list)
print()
print("Cleaning Reddit comments...")
reddit_comment_list = clean(reddit_comment_list)
print(reddit_comment_list)
print()
print("Cleaning article...")
article = clean_text(article)
print(article)
print()
print("Cleaning brochure...")
brochure = clean_text(brochure)
print(brochure)
print()
print("Cleaning textbook...")
textbook = clean_text(textbook)
print(textbook)

Cleaning Youtube comments...
['i went in this airline the service was not good i almost slept the whole flight without eating and entertainment but i guess every airline does not have tv is so i just decided airlines with tv is is not always the best i learned my lesson the non tv is are the same as tv is for a good 787 is the first scoot flight i had i think they should have these planes to bring back 747 757 a340 a380 717 727 737 232', 'i love the idea of silent economy which is just economy plus with no children screaming ', 'thanks for your video one question which kind of plug your seat had was that compatible with a c type thanks ', 'i will be your guide on how to survive scoot long haul flights 1 bring a power bank fully charged 2 bring some snacks with you onboard 3 bring a gaming handheld to play some games to kill some time 4 bring your own amenities like eye masks earplugs toothbrushes and toothpaste', 'one hour in economy flight', 'for me 4 hours it can be very uncomfortabl

In [66]:
""" Saving clean files! """
import pickle

""" Youtube """
file = "youtube"

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))
pickle.dump(youtube_comment_list, open("support/%s/%s/comment_list.pkl" % (search_terms, file), "wb"))

""" Reddit """
file = "reddit"

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))
pickle.dump(reddit_comment_list, open("support/%s/%s/comment_list.pkl" % (search_terms, file), "wb"))

""" article """
file = "article"

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))
pickle.dump(article, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))

""" Brochure """
file = "brochure"

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))
pickle.dump(brochure, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))

""" Textbook """
file = "textbook"

pickle.dump(search_terms, open("support/%s/searchTerms.pkl" % search_terms, "wb"))
pickle.dump(textbook, open("support/%s/%s/%s.pkl" % (search_terms, file, file), "wb"))